# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [30 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 25.29 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f769a7eb2d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 30
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 30, 'EVs_n_max': 1566, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  31676.2 , over-consume=kWh  47066.75 , under-consume=kWh  15390.55 , Total_cost=€  1197.51 , overcost=€  1647.38 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  30633.79 , over-consume=kWh  46045.09 , under-consume=kWh  15411.3 , Total_cost=€  1183.55 , overcost=€  1623.23 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -1690.86 , over-consume=KWh  1357.48 , under-consume=KWh  3048.34 , Total_cost=€  -32.38 , Overcost=€  47.13 
 EV_INFO: Av.EV_energy_leaving=kWh  62.85 , Std.EV_energy_leaving=kWh  24.09 , EV_departures =  1563 , EV_queue_left =  2
SCORE:  Cumulative_reward= 471355.24 - Step_rewars (load_t= 432454.59, EVs_energy_t= 3994.93)
 - Final_rewards (EVs_energy= 20754.54, Overconsume= -387.0, Underconsume= 55.03, Overcost= 14483.17)
Episode:1 Score:471355.2448447527


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  41.393532  64.154404  59.762733  37.871044   
2022-01-01 00:15:00  41.643532  63.476543  59.084873  38.121044   
2022-01-01 00:30:00  41.893532  63.026611  58.634941   0.000000   
2022-01-01 00:45:00  41.643532  62.776611  58.384941   0.000000   
2022-01-01 01:00:00  41.327328  63.026611  58.068737   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  99.989998  26.145203  66.114548  99.989998   
2022-06-06 05:00:00  99.989998  25.895203  67.143585  99.989998   
2022-06-06 05:15:00  99.989998  25.645203  68.227036  99.989998   
2022-06-06 05:30:00  99.989998  25.395203  69.260818  99.989998   
2022-06-06 05:45:00  99.989998  25.145203  70.271156  99.989998   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [4689, 4687, 4688, 4686]  [1, 2, 2, 1]   
2022-01-01 00:30:00     [4689, 4687, 4688, 0]  [2, 2, 2, 2]   
2022-01-01 00:45:00     [4689, 4687, 4688, 0]  [2, 1, 2, 2]   
2022-01-01 01:00:00     [4689, 4687, 4688, 0]  [2, 2, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [5379, 5378, 5381, 5380]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [5379, 5378, 5381, 5380]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [5379, 5378, 5381, 5380]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [5379, 5378, 5381, 5380]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [5379, 5378, 5381, 5380]  [1, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00     [True, True, True, False]        2.000000   
2022-01-01 00:45:00    [True, False, True, False]        0.000000   
2022-01-01 01:00:00     [True, True, True, False]        1.000000   
...                                           ...             ...   
2022-06-06 04:45:00   [False, False, True, False]        3.045520   
2022-06-06 05:00:00   [False, False, True, False]        4.116158   
2022-06-06 05:15:00   [False, False, True, False]        4.333804   
2022-06-06 05:30:00   [False, False, True, False]        4.135138   
2022-06-06 05:45:00   [False, False, True, False]        4.041369   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  3.145970e+00    15.000000    0.00000   
2022-01-01 00:15:00          -5.422896  0.000000e+00    15.000000 -100.47057   
2022-01-01 00:30:00          -3.599464 -2.220446e-16    -1.571369    0.00000   
2022-01-01 00:45:00          -3.000000 -1.942822e+00    15.000000    0.00000   
2022-01-01 01:00:00          -2.529639  0.000000e+00    -1.504038    0.00000   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000 -6.090989e+00    -8.847514    0.00000   
2022-06-06 05:00:00          -1.000000 -8.232266e+00    -9.243233    0.00000   
2022-06-06 05:15:00          -1.000000 -8.667556e+00    -8.882022    0.00000   
2022-06-06 05:30:00          -1.000000 -8.270225e+00    -8.711533    0.00000   
2022-06-06 05:45:00          -1.000000 -8.082686e+00    -9.201925    0.00000   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00 -85.470570  
2022-01-01 00:30:00  -1.571369  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  -1.504038  
...                        ...  
2022-06-06 04:45:00  -8.847514  
2022-06-06 05:00:00  -9.243233  
2022-06-06 05:15:00  -8.882022  
2022-06-06 05:30:00  -8.711533  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6261, Arrival time: 2022-01-01 13:45:00, Parking_time: 22.419965709129233, Leaving_time: 2022-01-02 12:10:11.876553, SOC: 0.5714216473917084, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7825, Arrival time: 2022-12-31 16:00:00, Parking_time: 22.712438395013447, Leaving_time: 2023-01-01 14:42:44.778222, SOC: 0.5094962125863846, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21818.93 , over-consume=kWh  42353.29 , under-consume=kWh  20534.36 , Total_cost=€  1009.97 , overcost=€  1853.28 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21897.92 , over-consume=kWh  42153.37 , under-consume=kWh  20255.45 , Total_cost=€  1019.2 , overcost=€  1847.2 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3437.18 , over-consume=KWh  948.31 , under-consume=KWh  4385.5 , Total_cost=€  -116.94 , Overcost=€  43.15 
 EV_INFO: Av.EV_energy_leaving=kWh  67.52 , Std.EV_energy_leaving=kWh  23.41 , EV_departures =  1562 , EV_queue_left =  0
SCORE:  Cumulative_reward= 487916.28 - Step_rewars (load_t= 420164.38, EVs_energy_t= 28572.28)
 - Final_rewards (EVs_energy= 24029.45, Overconsume= -101.91, Underconsume= -309.55, Overcost= 15561.63)
Episode:1 Score:487916.28116211924


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  51.755856  57.287075  87.761681   0.000000   
2022-06-06 05:00:00  53.587673  57.287075  89.593498   0.000000   
2022-06-06 05:15:00  55.539665  57.287075  91.545494   0.000000   
2022-06-06 05:30:00  57.138016  57.287075  93.143845   0.000000   
2022-06-06 05:45:00  58.869240  57.287075  94.875069  44.303707   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00      [10072, 10073, 10071, 0]  [1, 0, 1, 2]   
2022-06-06 05:00:00      [10072, 10073, 10071, 0]  [1, 0, 1, 2]   
2022-06-06 05:15:00      [10072, 10073, 10071, 0]  [1, 0, 1, 2]   
2022-06-06 05:30:00      [10072, 10073, 10071, 0]  [1, 0, 1, 2]   
2022-06-06 05:45:00  [10072, 10073, 10071, 10074]  [1, 1, 1, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, True, True, False]       10.487891   
2022-06-06 05:00:00    [True, True, True, False]       14.654533   
2022-06-06 05:15:00   [True, True, False, False]       15.615937   
2022-06-06 05:30:00   [True, True, False, False]       12.786801   
2022-06-06 05:45:00   [True, True, False, False]       13.849805   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -4.179119    -5.481191        0.0   
2022-01-01 00:15:00                0.0 -4.529310    -5.267023        0.0   
2022-01-01 00:30:00                0.0 -4.293726    -4.743412        0.0   
2022-01-01 00:45:00                0.0 -3.846047    -4.256834        0.0   
2022-01-01 01:00:00                0.0 -3.554101    -3.026399        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.481191  
2022-01-01 00:15:00  -5.267023  
2022-01-01 00:30:00  -4.743412  
2022-01-01 00:45:00  -4.256834  
2022-01-01 01:00:00  -3.026399  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 10956, Arrival time: 2022-01-01 08:30:00, Parking_time: 23.02777006233985, Leaving_time: 2022-01-02 07:31:39.972224, SOC: 0.47152943605845166, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 12520, Arrival time: 2022-12-31 21:30:00, Parking_time: 21.608506570516557, Leaving_time: 2023-01-01 19:06:30.623654, SOC: 0.4067509801300336, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17789.9 , over-consume=kWh  39210.8 , under-consume=kWh  21420.9 , Total_cost=€  853.87 , overcost=€  1638.49 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18685.05 , over-consume=kWh  39744.65 , under-consume=kWh  21059.6 , Total_cost=€  892.95 , overcost=€  1661.53 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4637.66 , over-consume=KWh  701.02 , under-consume=KWh  5338.68 , Total_cost=€  -163.64 , Overcost=€  29.24 
 EV_INFO: Av.EV_energy_leaving=kWh  69.07 , Std.EV_energy_leaving=kWh  23.02 , EV_departures =  1561 , EV_queue_left =  0
SCORE:  Cumulative_reward= 486462.91 - Step_rewars (load_t= 409044.94, EVs_energy_t= 35932.27)
 - Final_rewards (EVs_energy= 23470.93, Overconsume= 2361.86, Underconsume= -1003.19, Overcost= 16656.12)
Episode:1 Score:486462.9146899894


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  76.076302  27.954609  53.349506  72.663696   
2022-06-06 03:45:00  76.460808  27.704609  53.734013  73.048203   
2022-06-06 04:00:00  77.107086  27.454609  54.380291  73.694481   
2022-06-06 04:15:00  77.772537  27.204609  55.045746  74.359932   
2022-06-06 04:30:00  54.329250  26.954609  55.553234  74.867424   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 0, 1, 2]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [14731, 14733, 14734, 14732]  [1, 2, 1, 1]   
2022-06-06 03:45:00  [14731, 14733, 14734, 14732]  [1, 2, 1, 1]   
2022-06-06 04:00:00  [14731, 14733, 14734, 14732]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [14731, 14733, 14734, 14732]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [14735, 14733, 14734, 14732]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, True, False, False]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00    [True, False, True, True]        5.420920   
2022-06-06 03:45:00    [True, False, True, True]        4.614062   
2022-06-06 04:00:00    [True, False, True, True]        7.755329   
2022-06-06 04:15:00    [True, False, True, True]        7.985449   
2022-06-06 04:30:00    [True, False, True, True]        6.089861   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -2.410988    -4.691989   0.000000   
2022-01-01 00:15:00                0.0 -3.815194    -6.176884   0.000000   
2022-01-01 00:30:00                0.0 -5.294572    -3.210135   0.000000   
2022-01-01 00:45:00                0.0 -2.926081    -5.501674   0.000000   
2022-01-01 01:00:00                0.0 -4.551841    -7.276184   0.000000   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00               -1.0  0.000000    15.000000   0.000000   
2022-06-06 03:45:00               -1.0  0.000000    15.000000   0.000000   
2022-06-06 04:00:00               -1.0  0.000000    15.000000   0.000000   
2022-06-06 04:15:00               -1.0  0.000000    15.000000  94.330122   
2022-06-06 04:30:00               -1.0  0.000000    15.000000   0.000000   

                        rewards  
time                             
2022-01-01 00:00:00   -4.691989  
2022-01-01 00:15:00   -6.176884  
2022-01-01 00:30:00   -3.210135  
2022-01-01 00:45:00   -5.501674  
2022-01-01 01:00:00   -7.276184  
...                         ...  
2022-06-06 03:30:00   15.000000  
2022-06-06 03:45:00   15.000000  
2022-06-06 04:00:00   15.000000  
2022-06-06 04:15:00  109.330122  
202

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()